In [1]:
import warnings
import os

from sympy import Symbol
from numpy.testing import assert_allclose
import numpy as np
from pycalphad import Database, Model, calculate, equilibrium, EquilibriumError, ConditionError
from pycalphad.codegen.callables import build_callables
from pycalphad.core.solver import SolverBase, Solver
from pycalphad.core.utils import get_state_variables
import pycalphad.variables as v
from pycalphad.tests.datasets import *

warnings.simplefilter("always", UserWarning) # so we can test warnings


In [2]:
AL2O3_ND2O3_ZRO2_DBF = Database(AL2O3_ND2O3_ZRO2_TDB)
alfeo=Database("Al-Fe-O_Lindwall_etal.TDB")

/Users/sunhui/Desktop/new-charge/pycalphad/pycalphad/io/tdb.py:974: UserWarning: The type definition character `W` was defined in the following phases: ['BCC_B2'], but no corresponding TYPE_DEFINITION line was found in the TDB.
  warnings.warn(f"The type definition character `{typechar}` was defined in the following phases: "


In [3]:
def test_charge_balance_constraint():
    """Phases with charged species are correctly calculated and charged balanced in equilibrium"""
    comps = ['FE', 'AL', 'O', 'VA']
    #phases = list(AL2O3_ND2O3_ZRO2_DBF.phases.keys())
    phases = ['HALITE']
    conds = {v.P: 101325, v.N: 1, v.T: 500, v.X('FE'): 0.2, v.X('O'): 0.6}
    # Higher point density is required for convergence. Lower point densities
    # Can result in either no phases, or only FLUO phase (incorrect)
    res = equilibrium(alfeo, comps, phases, conds, calc_opts={'pdens':2000}, verbose=True)
    # Values below checked with Thermo-Calc
    print('a=',res.GM.values)
    print(res.Y.values.squeeze())
    #assert np.allclose(res.NP.values.squeeze()[:2], [0.30164254, 0.69835646])
    # site fractions of ND2O3_A
    Y_ND2O3_A = res.Y.values.squeeze()[0, :5]
    Y_PYRO = res.Y.values.squeeze()[1, :]
    SPEC_CHG_ND2O3_A = np.array([3, 4, -2, -2, 0])  # (ND+3,ZR+4):(O-2):(O-2,VA)
    SITE_RATIO_ND2O3_A = np.array([2, 2, 3, 1, 1])  # 2:3:1
    SPEC_CHG_PYRO = np.array([3, 4, 3, 4, -2, 0, -2, -2, 0])  # (ND+3,ZR+4):(ND+3,ZR+4):(O-2,VA):(O-2):(O-2,VA)
    SITE_RATIO_PYRO = np.array([2, 2, 2, 2, 6, 6, 1, 1, 1])  # 2:2:6:1:1
    CHG_ND2O3_A = np.dot(Y_ND2O3_A*SPEC_CHG_ND2O3_A, SITE_RATIO_ND2O3_A)
    CHG_PYRO = np.dot(Y_PYRO*SPEC_CHG_PYRO, SITE_RATIO_PYRO)
    print('CHARGE ND2O3_A', CHG_ND2O3_A)
    print('CHARGE PYRO', CHG_PYRO)
    #assert np.isclose(CHG_ND2O3_A, 0)
    #assert np.isclose(CHG_PYRO, 0)
    print(Y_ND2O3_A)
    assert np.allclose(Y_ND2O3_A, [9.79497936e-01, 2.05020639e-02, 1.00000000e+00, 2.05020639e-02, 9.79497936e-01], rtol=5e-4)
    assert np.allclose(Y_PYRO, [9.99970071e-01, 2.99288042e-05, 3.83395063e-02, 9.61660494e-01, 9.93381787e-01, 6.61821340e-03, 1.00000000e+00, 1.39970285e-03, 9.98600297e-01], rtol=5e-4)


In [4]:
a=test_charge_balance_constraint()

Components: AL AL+3 AL1O1 AL1O2 AL2 AL2FE1O4 AL2O AL2O1 AL2O2 AL2O3 ALO ALO2 ALO3/2 FE FE+2 FE+3 FE+4 FE1O1 FE1O2 FE2 FE2O3 FEO FEO3/2 O O-2 O2 O3 VA
Phases: HALITE 
[done]
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)
compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
va 0.002771569260075629
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)
compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
va 0.0037079741679310607
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], N

compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
Yes1
va 0.0038416899344285715
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)
compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
Yes1
va 0.004143066287852659
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)
compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
va 0.0007999193293407592
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.592068605497

compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)
compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
va 0.041696315564358266
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)
compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
Yes1
va 0.022601526232671088
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)
compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
va 0.

va 0.5234774917273107
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)
compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
va 0.002738613688810454
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)
compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
va 0.010208376425519694
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-21812

compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)
compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
Yes1
va 0.0008708720028542949
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)
compset 2 CompositionSet(HALITE, [0.12332077 0.24268833 0.6339909 ], NP=0.30935042583191175, GM=-204617.04519082946)
Yes1
va 0.0004989376280229996
Yes3
compset 0 CompositionSet(HALITE, [0.24960318 0.1713745  0.57902232], NP=0.5920686054979991, GM=-275676.9308584439)
compset 1 CompositionSet(HALITE, [0.14270971 0.23796479 0.6193255 ], NP=0.09858096867008913, GM=-218126.60520943857)


...

compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
Yes1
va 0.6454310174828789
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
Yes1
va 0.0852102199521304
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
va 0.6248109011418836
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
va 0.20743771416936296
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.739

compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
va 0.1139880823158447
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
va 0.15147602355860992
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
va 0.14172090735150347
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
va 0.09726230199346839
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset

compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
va 0.24040797500175232
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
Yes1
va 0.2419522213864746
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
Yes1
va 0.47080215796557356
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-308237.73942526977)
Yes1
va 0.3480315944960648
Yes3
compset 0 CompositionSet(HALITE, [0.2 0.2 0.6], NP=0.999999999994712, GM=-248139.93799057146)
compset 1 CompositionSet(HALITE, [0.25012506 0.24987494 0.5       ], NP=1e-06, GM=-3082

a= [[[[[nan]]]]]
[[nan nan nan nan nan]
 [nan nan nan nan nan]
 [nan nan nan nan nan]
 [nan nan nan nan nan]]


ValueError: operands could not be broadcast together with shapes (5,) (9,) 

In [ ]:
a=test_charge_balance_constraint()

In [ ]:
model=Model(AL2O3_ND2O3_ZRO2_DBF,comps = ['ND', 'ZR', 'O', 'VA'],phase_name = 'ND2O3_A')

In [2]:
          ys=ys-chargefact*phr(jj)%invmat(nj,phr(jj)%idim)*&
               phr(jj)%curd%netcharge

SyntaxError: invalid syntax (2914376038.py, line 1)

In [5]:
import warnings
import os
import pytest
from sympy import Symbol
from numpy.testing import assert_allclose
import numpy as np
from pycalphad import Database, Model, calculate, equilibrium, EquilibriumError, ConditionError
from pycalphad.codegen.callables import build_callables, build_phase_records
from pycalphad.core.solver import SolverBase, Solver
from pycalphad.core.utils import get_state_variables, instantiate_models
import pycalphad.variables as v
from pycalphad.tests.datasets import *
ROSE_DBF = Database(ROSE_TDB)
ALFE_DBF = Database(ALFE_TDB)
ALNIFCC4SL_DBF = Database(ALNIFCC4SL_TDB)
ALCOCRNI_DBF = Database(ALCOCRNI_TDB)
ISSUE43_DBF = Database(ISSUE43_TDB)
TOUGH_CHEMPOT_DBF = Database(ALNI_TOUGH_CHEMPOT_TDB)
NI_AL_DUPIN_2001_DBF = Database(NI_AL_DUPIN_2001_TDB)
CUO_DBF = Database(CUO_TDB)
PBSN_DBF = Database(PBSN_TDB)
AL_PARAMETER_DBF = Database(AL_PARAMETER_TDB)
CUMG_PARAMETERS_DBF = Database(CUMG_PARAMETERS_TDB)


@pytest.mark.solver
def test_rose_nine():
    "Nine-component rose diagram point equilibrium calculation."
    my_phases_rose = ['TEST']
    comps = ['H', 'HE', 'LI', 'BE', 'B', 'C', 'N', 'O', 'F']
    conds = dict({v.T: 1000, v.P: 101325})
    for comp in comps[:-1]:
        conds[v.X(comp)] = 1.0/float(len(comps))
    eqx = equilibrium(ROSE_DBF, comps, my_phases_rose, conds, verbose=True)
    assert_allclose(eqx.GM.values.flat[0], -5.8351e3, atol=0.1)


@pytest.mark.solver
def test_eq_binary():
    "Binary phase diagram point equilibrium calculation with magnetism."
    my_phases = ['LIQUID', 'FCC_A1', 'HCP_A3', 'AL5FE2',
                 'AL2FE', 'AL13FE4', 'AL5FE4']
    comps = ['AL', 'FE', 'VA']
    conds = {v.T: 1400, v.P: 101325, v.X('AL'): 0.55}
    eqx = equilibrium(ALFE_DBF, comps, my_phases, conds, verbose=True)
    assert_allclose(eqx.GM.values.flat[0], -9.608807e4)
def test_eq_single_phase():
    "Equilibrium energy should be the same as for a single phase with no miscibility gaps."
    res = calculate(ALFE_DBF, ['AL', 'FE'], 'LIQUID', T=[1400, 2500], P=101325,
                    points={'LIQUID': [[0.1, 0.9], [0.2, 0.8], [0.3, 0.7],
                                       [0.7, 0.3], [0.8, 0.2]]})
    eq = equilibrium(ALFE_DBF, ['AL', 'FE'], 'LIQUID',
                     {v.T: [1400, 2500], v.P: 101325,
                      v.X('AL'): [0.1, 0.2, 0.3, 0.7, 0.8]}, verbose=True)
    assert_allclose(np.squeeze(eq.GM), np.squeeze(res.GM), atol=0.1)


/Users/sunhui/Desktop/new-charge/pycalphad/pycalphad/io/tdb.py:974: UserWarning: The type definition character `'` was defined in the following phases: ['FCC_A1'], but no corresponding TYPE_DEFINITION line was found in the TDB.
  warnings.warn(f"The type definition character `{typechar}` was defined in the following phases: "
/Users/sunhui/Desktop/new-charge/pycalphad/pycalphad/io/tdb.py:974: UserWarning: The type definition character `%` was defined in the following phases: ['FCC_A1'], but no corresponding TYPE_DEFINITION line was found in the TDB.
  warnings.warn(f"The type definition character `{typechar}` was defined in the following phases: "


In [6]:
test_eq_single_phase()

Components: AL FE
Phases: LIQUID 
[done]
compset 0 CompositionSet(LIQUID, [0.10204082 0.89795918], NP=0.7860110765919384, GM=-79385.23411016162)
compset 1 CompositionSet(LIQUID, [0.0925038 0.9074962], NP=0.21398892340806164, GM=-78616.66432024709)
compset 0 CompositionSet(LIQUID, [0.10204082 0.89795918], NP=0.7860110765919384, GM=-79385.23411016162)
compset 1 CompositionSet(LIQUID, [0.0925038 0.9074962], NP=0.21398892340806164, GM=-78616.66432024709)
compset 0 CompositionSet(LIQUID, [0.10204082 0.89795918], NP=0.7860110765919384, GM=-79385.23411016162)
compset 1 CompositionSet(LIQUID, [0.0925038 0.9074962], NP=0.21398892340806164, GM=-78616.66432024709)
compset 0 CompositionSet(LIQUID, [0.10204082 0.89795918], NP=0.7860110765919384, GM=-79385.23411016162)
compset 1 CompositionSet(LIQUID, [0.0925038 0.9074962], NP=0.21398892340806164, GM=-78616.66432024709)
compset 0 CompositionSet(LIQUID, [0.10204082 0.89795918], NP=0.7860110765919384, GM=-79385.23411016162)
compset 1 CompositionSet(LI

In [6]:
a=np.array([-1,2,-2,3])

In [1]:
! pytest test_equilibrium.py

============================= test session starts ==============================
platform darwin -- Python 3.9.7, pytest-6.2.5, py-1.10.0, pluggy-1.0.0
rootdir: /Users/sunhui/Desktop/new-charge/pycalphad, configfile: pyproject.toml
plugins: cov-2.12.1
collected 50 items                                                             

test_equilibrium.py ...........F......FF..F...............s....F.FFFF.   [100%]

=================================== FAILURES ===================================
_______________________ test_eq_illcond_magnetic_hessian _______________________

    @pytest.mark.solver
    def test_eq_illcond_magnetic_hessian():
        """
        Check equilibrium of a system with an ill-conditioned Hessian due to magnetism (Tc->0).
        This is difficult to reproduce so we only include some known examples here.
        """
        # This set of conditions is known to trigger the issue
        eq = equilibrium(ALFE_DBF, ['AL', 'FE', 'VA'], ['FCC_A1', 'AL13FE4'],
          

 CompositionSet(AL13FE4, [0.75751514 0.24248486], NP=1e-06, GM=-35805.854396523304)]
site [1.00000000e+00 1.00000000e+05 3.00000000e+02 9.99999961e-01
 3.93890037e-08 1.00000000e+00]
len 6 4
compset [CompositionSet(FCC_A1, [0.8 0.2], NP=1.0, GM=-17803.320902447096)
 CompositionSet(AL13FE4, [0.75751514 0.24248486], NP=1e-06, GM=-35805.854396523304)]
site [1.00000000e+00 1.00000000e+05 3.00000000e+02 1.00000000e+00
 1.00000000e+00 5.98012292e-10 1.32327322e-13]
len 7 6
charge_factor
Yes2 5.975652276464285e-10
Yes3
ori_x [1.00000000e+00 1.00000000e+05 3.00000000e+02 9.99998607e-01
 1.39317189e-06 1.00000000e+00]
change_x [1.00000000e+00 1.00000000e+05 3.00000000e+02 9.99998607e-01
 1.39317189e-06 1.00000000e+00]
ori_x [1.00000000e+00 1.00000000e+05 3.00000000e+02 1.00000000e+00
 1.00000000e+00 4.47064623e-13 1.00000000e-14]
change_x [1.00000000e+00 1.00000000e+05 3.00000000e+02 1.00000000e+00
 1.00000000e+00 4.47064623e-13 1.00000000e-14]
compset [CompositionSet(FCC_A1, [0.8 0.2], NP=1.0,

site [1.00000000e+00 1.01325000e+05 1.52300000e+03 2.67553772e-10
 1.34077809e-10 2.00213945e-10 9.99999999e-01 2.67553772e-10
 1.34077982e-10 2.00214110e-10 9.99999999e-01 1.00000000e-14]
len 12 11
charge_factor
compset [CompositionSet(BCC_B2, [0.5        0.37755102 0.12244898], NP=0.2850769230781869, GM=-115802.62946711856)
 CompositionSet(BCC_B2, [0.5       0.3877551 0.1122449], NP=0.2969572649560259, GM=-116395.23107457293)
 CompositionSet(BCC_B2, [3.67346939e-01 1.00000000e-14 6.32653061e-01], NP=0.41796581196578725, GM=-89615.28710330275)
 CompositionSet(LIQUID, [0.45700484 0.18296174 0.36003342], NP=0.0, GM=-102305.64155318434)]
site [1.00000000e+00 1.01325000e+05 1.52300000e+03 2.67553772e-10
 1.34077809e-10 2.00213945e-10 9.99999999e-01 2.67553772e-10
 1.34077963e-10 2.00214107e-10 9.99999999e-01 1.00000000e-14]
len 12 11
charge_factor
compset [CompositionSet(BCC_B2, [0.5        0.37755102 0.12244898], NP=0.2850769230781869, GM=-115802.62946711856)
 CompositionSet(BCC_B2, [0.5

 CompositionSet(LIQUID, [0.45700484 0.18296174 0.36003342], NP=0.0, GM=-102305.64155318434)]
site [1.00000000e+00 1.01325000e+05 1.52300000e+03 2.18112584e-10
 1.09301607e-10 1.63216465e-10 1.00000000e+00 2.18112584e-10
 1.09301607e-10 1.63216465e-10 1.00000000e+00 1.00000000e-14]
len 12 11
charge_factor
compset [CompositionSet(BCC_B2, [0.5        0.37755102 0.12244898], NP=0.2850769230781869, GM=-115802.62946711856)
 CompositionSet(BCC_B2, [0.5       0.3877551 0.1122449], NP=0.2969572649560259, GM=-116395.23107457293)
 CompositionSet(BCC_B2, [3.67346939e-01 1.00000000e-14 6.32653061e-01], NP=0.41796581196578725, GM=-89615.28710330275)
 CompositionSet(LIQUID, [0.45700484 0.18296174 0.36003342], NP=0.0, GM=-102305.64155318434)]
site [1.00000000e+00 1.01325000e+05 1.52300000e+03 2.18112584e-10
 1.09301607e-10 1.63216465e-10 1.00000000e+00 2.18112584e-10
 1.09301607e-10 1.63216465e-10 1.00000000e+00 1.00000000e-14]
len 12 11
charge_factor
compset [CompositionSet(BCC_B2, [0.5        0.3775

ori_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.00000000e-14]
change_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.00000000e-14]
ori_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.00000000e-14]
change_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.56633541e-10
 7.84929391e-11 1.17210903e-10 1.00000000e+00 1.00000000e-14]
ori_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 5.67247455e-01
 4.22023438e-01 1.07291064e-02]
change_x [1.00000000e+00 1.01325000e+05 1.52300000e+03 5.67247455e-01
 4.22023438e-01 1.07291064e-02]
compset [CompositionSet(BCC_B2, [

compset [CompositionSet(BCC_B2, [0.5        0.37755102 0.12244898], NP=0.2850769230781869, GM=-115802.62946711856)
 CompositionSet(BCC_B2, [0.5       0.3877551 0.1122449], NP=0.2969572649560259, GM=-116395.23107457293)
 CompositionSet(BCC_B2, [3.67346939e-01 1.00000000e-14 6.32653061e-01], NP=0.41796581196578725, GM=-89615.28710330275)
 CompositionSet(LIQUID, [0.45700484 0.18296174 0.36003342], NP=0.0, GM=-102305.64155318434)]
site [1.00000000e+00 1.01325000e+05 1.52300000e+03 9.55844186e-11
 4.78997149e-11 7.15270555e-11 1.00000000e+00 9.55844186e-11
 4.78997149e-11 7.15270555e-11 1.00000000e+00 1.00000000e-14]
len 12 11
charge_factor
compset [CompositionSet(BCC_B2, [0.5        0.37755102 0.12244898], NP=0.2850769230781869, GM=-115802.62946711856)
 CompositionSet(BCC_B2, [0.5       0.3877551 0.1122449], NP=0.2969572649560259, GM=-116395.23107457293)
 CompositionSet(BCC_B2, [3.67346939e-01 1.00000000e-14 6.32653061e-01], NP=0.41796581196578725, GM=-89615.28710330275)
 CompositionSet(LI

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [9]:
x=a[2:]/2

In [18]:
a[1:].*a[1:]

SyntaxError: invalid syntax (3380728885.py, line 1)